In [ ]:
from pynq import DefaultHierarchy

class fftDriver(DefaultHierarchy):
    def __init__(self, description):
        super().__init__(description)
    def fft_acc(self, data):
        with xlnk.cma_array(shape=(len(data,),), dtype=np.float64) as in_buffer,\
             xlnk.cma_array(shape=(len(data,),), dtype=np.float64) as out_buffer:
            np.copyto(in_buffer, data)
            self.axi_dma_0.sendchannel.transfer(in_buffer)
            self.axi_dma_0.recvchannel.transfer(out_buffer)
            self.axi_dma_0.sendchannel.wait()
            self.axi_dma_0.recvchannel.wait()
            result = out_buffer.copy()
        return result
    
    @staticmethod
    def checkhierarchy(description):
        if 'xfft_0' in description['ip'] \
             and 'axi_dma_0' in description['ip']:
                return True
        return False

In [ ]:
from pynq import Overlay
import pynq.lib.dma
overlay= Overlay('/home/xilinx/jupyter_notebooks/common/add/fft_acc.bit')
dma = overlay.FFT.axi_dma_0

In [ ]:
chirp_ad_values=[1, 2, 2, 3, 4, 5, 6, 15, 78, 52, 98]

In [ ]:
from pynq import Xlnk
import time
xlnk=Xlnk()

in_buffer=xlnk.cma_array(shape=(n,), dtype=np.int32)
out_buffer=xlnk.cma_array(shape=(n,), dtype=np.int32)

np.copyto(in_buffer,chirp_ad_values)


dma.sendchannel.transfer(in_buffer)
dma.recvchannel.transfer(out_buffer)
dma.sendchannel.wait()
dma.sendrecvchannel.wait()
stop_time=time.time()
hw_exec_time=stop_time-start_time

print('hardware execution time',hw_exec_time)


in_buffer.close()
out_buffer.close()